In [2]:
!pip install pytesseract tensorflow

In [4]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [5]:
!apt install tesseract-ocr

# Install pytesseract
!pip install pytesseract

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
tesseract-ocr is already the newest version (4.1.1-2.1build1).
0 upgraded, 0 newly installed, 0 to remove and 11 not upgraded.


In [6]:
import os
import cv2
import numpy as np
import pandas as pd
import tensorflow as tf
import pytesseract as pt
import plotly.express as px
import matplotlib.pyplot as plt
import xml.etree.ElementTree as xet
from PIL import Image
from glob import glob
from skimage import io
from shutil import copy
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import TensorBoard
from sklearn.model_selection import train_test_split
from tensorflow.keras.applications import InceptionResNetV2
from tensorflow.keras.layers import Dense, Dropout, Flatten, Input
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.callbacks import ModelCheckpoint
tesseract_path = "/content/tesseract"
# Add the Tesseract directory to the system PATH
os.environ["PATH"] += os.pathsep + tesseract_path

# Set Tesseract path for pytesseract
pt.pytesseract.tesseract_cmd = '/usr/bin/tesseract'



In [7]:
path = glob('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/*.xml')
labels_dict = dict(filepath=[],xmin=[],xmax=[],ymin=[],ymax=[])
for filename in path:

    info = xet.parse(filename)
    root = info.getroot()
    member_object = root.find('object')
    labels_info = member_object.find('bndbox')
    xmin = int(labels_info.find('xmin').text)
    xmax = int(labels_info.find('xmax').text)
    ymin = int(labels_info.find('ymin').text)
    ymax = int(labels_info.find('ymax').text)

    labels_dict['filepath'].append(filename)
    labels_dict['xmin'].append(xmin)
    labels_dict['xmax'].append(xmax)
    labels_dict['ymin'].append(ymin)
    labels_dict['ymax'].append(ymax)

In [8]:
df = pd.DataFrame(labels_dict)
df.to_csv('labels.csv',index=False)
df

filepath  xmin  xmax  ymin  ymax
0    /content/drive/MyDrive/Number_Plate_Detection_...   137   262   249   290
1    /content/drive/MyDrive/Number_Plate_Detection_...    15   200    33   126
2    /content/drive/MyDrive/Number_Plate_Detection_...   131   187   130   144
3    /content/drive/MyDrive/Number_Plate_Detection_...    39   108   129   157
4    /content/drive/MyDrive/Number_Plate_Detection_...   813  1067   665   724
..                                                 ...   ...   ...   ...   ...
220  /content/drive/MyDrive/Number_Plate_Detection_...   456   651   722   778
221  /content/drive/MyDrive/Number_Plate_Detection_...    23   408   173   391
222  /content/drive/MyDrive/Number_Plate_Detection_...    66   174   302   332
223  /content/drive/MyDrive/Number_Plate_Detection_...    63   243   234   274
224  /content/drive/MyDrive/Number_Plate_Detection_...   385   746   293   434

[225 rows x 5 columns]

In [9]:
df[87:88]

filepath  xmin  xmax  ymin  ymax
87  /content/drive/MyDrive/Number_Plate_Detection_...    13   444   137   270

In [10]:
filename = df['filepath'][0]
def getFilename(filename):
    filename_image = xet.parse(filename).getroot().find('filename').text
    filepath_image = os.path.join('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images',filename_image)
    return filepath_image
getFilename(filename)

'/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N106.jpeg'

In [11]:
image_path = list(df['filepath'].apply(getFilename))
image_path[:10]

['/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N106.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N114.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N11.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N113.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N103.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N102.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N108.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N112.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/N105.jpeg',
 '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detec

In [12]:
file_path = image_path[87] #path of our image N2.jpeg
img = cv2.imread(file_path) #read the image
img = io.imread(file_path) #Read the image
fig = px.imshow(img)
fig.update_layout(width=600, height=500, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='Figure 8 - N2.jpeg with bounding box')
fig.add_shape(type='rect',x0=13, x1=444, y0=137, y1=270, xref='x', yref='y',line_color='cyan')
fig.show()
#a little example of what we expect from the model

In [24]:
labels = df.iloc[:,1:].values
data = []
output = []
for ind in range(len(image_path)):
    image = image_path[ind]
    img_arr = cv2.imread(image)
    h,w,d = img_arr.shape
    # Prepprocesing
    load_image = load_img(image,target_size=(224,224))
    load_image_arr = img_to_array(load_image)
    norm_load_image_arr = load_image_arr/255.0 # Normalization
    # Normalization to labels
    xmin,xmax,ymin,ymax = labels[ind]
    nxmin,nxmax = xmin/w,xmax/w
    nymin,nymax = ymin/h,ymax/h
    label_norm = (nxmin,nxmax,nymin,nymax) # Normalized output
    # Append
    data.append(norm_load_image_arr)
    output.append(label_norm)

In [ ]:
X = np.array(data,dtype=np.float32)
y = np.array(output,dtype=np.float32)

In [ ]:
x_train,x_test,y_train,y_test = train_test_split(X,y,train_size=0.8,random_state=0)
x_train.shape,x_test.shape,y_train.shape,y_test.shape

((180, 224, 224, 3), (45, 224, 224, 3), (180, 4), (45, 4))

In [ ]:
inception_resnet = InceptionResNetV2(weights="imagenet",include_top=False, input_tensor=Input(shape=(224,224,3)))
# ---------------------
headmodel = inception_resnet.output
headmodel = Flatten()(headmodel)
headmodel = Dense(550,activation="relu")(headmodel)
headmodel = Dense(200,activation="relu")(headmodel)
headmodel = Dropout(0.2)(headmodel)
headmodel = Dense(4,activation="sigmoid")(headmodel)


# ---------- model

model = Model(inputs=inception_resnet.input,outputs=headmodel)



219055592/219055592 [==============================] - 1s 0us/step


In [ ]:
model.compile(loss='mean_squared_error',optimizer=tf.keras.optimizers.Adam(learning_rate=1e-04))
model.summary()

In [ ]:
model_checkpoint = ModelCheckpoint(
    filepath='best_model.h5',
    monitor='val_loss',
    save_best_only=True,
    mode='min',
    verbose=1
)
history = model.fit(x=x_train,y=y_train,batch_size=10,epochs=180,
                    validation_data=(x_test,y_test),callbacks=[model_checkpoint])

In [ ]:
model.save('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/best_model.h5')

In [ ]:
model = tf.keras.models.load_model('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/best_model.h5')
print('Model loaded Sucessfully')

Model loaded Sucessfully


In [ ]:
path = '/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/TEST/TEST.jpeg'
image = load_img(path) # PIL object
image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
image1 = load_img(path,target_size=(224,224))
image_arr_224 = img_to_array(image1)/255.0  # Convert into array and get the normalized output

# Size of the orginal image
h,w,d = image.shape
print('Height of the image =',h)
print('Width of the image =',w)

Height of the image = 729
Width of the image = 901


In [ ]:
fig = px.imshow(image)
fig.update_layout(width=700, height=500,  margin=dict(l=10, r=10, b=10, t=10), xaxis_title='Figure 13 - TEST Image')

In [ ]:
image_arr_224.shape

(224, 224, 3)

In [ ]:
test_arr = image_arr_224.reshape(1,224,224,3)
test_arr.shape

(1, 224, 224, 3)

In [ ]:
coords = model.predict(test_arr)
coords

1/1 [==============================] - 4s 4s/step


array([[0.33617166, 0.6613688 , 0.64556307, 0.7535606 ]], dtype=float32)

In [ ]:
denorm = np.array([w,w,h,h])
coords = coords * denorm
coords = coords.astype(np.int32)
coords

array([[302, 595, 470, 549]], dtype=int32)

In [ ]:
xmin, xmax,ymin,ymax = coords[0]
pt1 =(xmin,ymin)
pt2 =(xmax,ymax)
print(pt1, pt2)

(302, 470) (595, 549)


In [ ]:
cv2.rectangle(image,pt1,pt2,(0,255,0),3)
fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10))

In [ ]:
cropped_image = image[ymin:ymax,xmin:xmax]
fig = px.imshow(cropped_image)
fig.update_layout(width=350, height=250, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='Figure 15 Cropped image')

In [ ]:
file_path = "/content/cropped_image.png"  # Replace with your desired file path

# Save the image
cv2.imwrite(file_path,cropped_image)

True

In [ ]:
def object_detection(path):

    # Read image
    image = load_img(path) # PIL object
    image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
    image1 = load_img(path,target_size=(224,224))

    # Data preprocessing
    image_arr_224 = img_to_array(image1)/255.0 # Convert to array & normalized
    h,w,d = image.shape
    test_arr = image_arr_224.reshape(1,224,224,3)

    # Make predictions
    coords = model.predict(test_arr)

    # Denormalize the values
    denorm = np.array([w,w,h,h])
    coords = coords * denorm
    coords = coords.astype(np.int32)

    # Draw bounding on top the image
    xmin, xmax,ymin,ymax = coords[0]
    pt1 =(xmin,ymin)
    pt2 =(xmax,ymax)
    print(pt1, pt2)
    cv2.rectangle(image,pt1,pt2,(0,255,0),3)
    return image, coords

image, cods = object_detection(path)

fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='Figure 14')

1/1 [==============================] - 3s 3s/step
(302, 470) (595, 549)


In [ ]:
from PIL import Image
import torchvision.transforms as transforms
import torch

# Load image
img = Image.open('cropped_image.png')

# Convert to PyTorch tensor
loader = transforms.ToTensor()
img_tensor = loader(img).unsqueeze(0)
import torch.nn.functional as F

# Upscale image
upscaled_img = F.interpolate(img_tensor, scale_factor=2, mode='bicubic', align_corners=False)
# Convert to PIL image
unloader = transforms.ToPILImage()
upscaled_img_pil = unloader(upscaled_img.squeeze(0))

# Save image
upscaled_img_pil.save('upscaled_image.png')

In [25]:
def parsing(path):
    parser = xet.parse(path).getroot()
    name = parser.find('filename').text
    filename = f'/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/images/{name}'

    # width and height
    parser_size = parser.find('size')
    width = int(parser_size.find('width').text)
    height = int(parser_size.find('height').text)

    return filename, width, height
df[['filename','width','height']] = df['filepath'].apply(parsing).apply(pd.Series)
df.head()

filepath  xmin  xmax  ymin  ymax  \
0  /content/drive/MyDrive/Number_Plate_Detection_...   137   262   249   290   
1  /content/drive/MyDrive/Number_Plate_Detection_...    15   200    33   126   
2  /content/drive/MyDrive/Number_Plate_Detection_...   131   187   130   144   
3  /content/drive/MyDrive/Number_Plate_Detection_...    39   108   129   157   
4  /content/drive/MyDrive/Number_Plate_Detection_...   813  1067   665   724   

                                            filename  width  height  
0  /content/drive/MyDrive/Number_Plate_Detection_...    610     485  
1  /content/drive/MyDrive/Number_Plate_Detection_...    250     166  
2  /content/drive/MyDrive/Number_Plate_Detection_...    275     183  
3  /content/drive/MyDrive/Number_Plate_Detection_...    400     300  
4  /content/drive/MyDrive/Number_Plate_Detection_...   1800    1200

In [26]:
df['center_x'] = (df['xmax'] + df['xmin'])/(2*df['width'])
df['center_y'] = (df['ymax'] + df['ymin'])/(2*df['height'])

df['bb_width'] = (df['xmax'] - df['xmin'])/df['width']
df['bb_height'] = (df['ymax'] - df['ymin'])/df['height']
df.head()

filepath  xmin  xmax  ymin  ymax  \
0  /content/drive/MyDrive/Number_Plate_Detection_...   137   262   249   290   
1  /content/drive/MyDrive/Number_Plate_Detection_...    15   200    33   126   
2  /content/drive/MyDrive/Number_Plate_Detection_...   131   187   130   144   
3  /content/drive/MyDrive/Number_Plate_Detection_...    39   108   129   157   
4  /content/drive/MyDrive/Number_Plate_Detection_...   813  1067   665   724   

                                            filename  width  height  center_x  \
0  /content/drive/MyDrive/Number_Plate_Detection_...    610     485  0.327049   
1  /content/drive/MyDrive/Number_Plate_Detection_...    250     166  0.430000   
2  /content/drive/MyDrive/Number_Plate_Detection_...    275     183  0.578182   
3  /content/drive/MyDrive/Number_Plate_Detection_...    400     300  0.183750   
4  /content/drive/MyDrive/Number_Plate_Detection_...   1800    1200  0.522222   

   center_y  bb_width  bb_height  
0  0.555670  0.204918   0.084536  
1  0.478916  0.740000   0.560241  
2  0.748634  0.203636   0.076503  
3  0.476667  0.172500   0.093333  
4  0.578750  0.141111   0.049167

In [27]:
!git clone https://github.com/ultralytics/yolov5

fatal: destination path 'yolov5' already exists and is not an empty directory.


In [14]:
!pip install -r ./yolov5/requirements.txt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 38.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 646.0/646.0 kB 63.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 7.6 MB/s eta 0:00:00
  Attempting uninstall: Pillow
    Found existing installation: Pillow 9.4.0
    Uninstalling Pillow-9.4.0:
      Successfully uninstalled Pillow-9.4.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
imageio 2.31.6 requires pillow<10.1.0,>=8.3.2, but you have pillow 10.1.0 which is incompatible.


In [3]:
!mkdir /content/yolov5/data_images/
!mkdir /content/yolov5/data_images/test/
!mkdir /content/yolov5/data_images/train/


In [28]:
df_train = df.iloc[:200]
df_test = df.iloc[200:]

In [29]:
train_folder = './yolov5/data_images/train'

values = df_train[['filename','center_x','center_y','bb_width','bb_height']].values
for fname, x,y, w, h in values:
    image_name = os.path.split(fname)[-1]
    txt_name = os.path.splitext(image_name)[0]

    dst_image_path = os.path.join(train_folder,image_name)
    dst_label_file = os.path.join(train_folder,txt_name+'.txt')

    # copy each image into the folder
    copy(fname,dst_image_path)

    # generate .txt which has label info
    label_txt = f'0 {x} {y} {w} {h}'
    with open(dst_label_file,mode='w') as f:
        f.write(label_txt)

        f.close()

test_folder = './yolov5/data_images/test'

values = df_test[['filename','center_x','center_y','bb_width','bb_height']].values
for fname, x,y, w, h in values:
    image_name = os.path.split(fname)[-1]
    txt_name = os.path.splitext(image_name)[0]

    dst_image_path = os.path.join(test_folder,image_name)
    dst_label_file = os.path.join(test_folder,txt_name+'.txt')

    # copy each image into the folder
    copy(fname,dst_image_path)

    # generate .txt which has label info
    label_txt = f'0 {x} {y} {w} {h}'
    with open(dst_label_file,mode='w') as f:
        f.write(label_txt)

        f.close()

In [30]:
!pip install GPUtil

  Preparing metadata (setup.py) ... done
  Created wheel for GPUtil: filename=GPUtil-1.4.0-py3-none-any.whl size=7395 sha256=448960d8ad4f0a5cd3d95a1605a0ca0105b07b7e50fdb95bc177b8579cf671c0
  Stored in directory: /root/.cache/pip/wheels/a9/8a/bd/81082387151853ab8b6b3ef33426e98f5cbfebc3c397a9d4d0
Successfully built GPUtil


In [31]:


import torch
from GPUtil import showUtilization as gpu_usage
from numba import cuda

def free_gpu_cache():
    print("Initial GPU Usage")
    gpu_usage()

    torch.cuda.empty_cache()

    cuda.select_device(0)
    cuda.close()
    cuda.select_device(0)

    print("GPU Usage after emptying the cache")
    gpu_usage()

free_gpu_cache()

Initial GPU Usage
| ID | GPU | MEM |
------------------
|  0 |  0% |  0% |
GPU Usage after emptying the cache
| ID | GPU | MEM |
------------------
|  0 |  1% |  1% |


In [33]:
!python ./yolov5/train.py --data /content/data.yaml --cfg ./yolov5/models/yolov5s.yaml --batch-size 8 --name Model --epochs 100

2023-11-29 09:14:53.156771: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-29 09:14:53.156839: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-29 09:14:53.156887: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
train: weights=yolov5/yolov5s.pt, cfg=./yolov5/models/yolov5s.yaml, data=/content/data.yaml, hyp=yolov5/data/hyps/hyp.scratch-low.yaml, epochs=100, batch_size=8, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, 

In [34]:
!python ./yolov5/export.py --weight ./yolov5/runs/train/Model/weights/best.pt --include torchscript onnx

export: data=yolov5/data/coco128.yaml, weights=['./yolov5/runs/train/Model/weights/best.pt'], imgsz=[640, 640], batch_size=1, device=cpu, half=False, inplace=False, keras=False, optimize=False, int8=False, dynamic=False, simplify=False, opset=17, verbose=False, workspace=4, nms=False, agnostic_nms=False, topk_per_class=100, topk_all=100, iou_thres=0.45, conf_thres=0.25, include=['torchscript', 'onnx']
YOLOv5 🚀 v7.0-247-g3f02fde Python-3.10.12 torch-2.1.0+cu118 CPU

Fusing layers... 
YOLOv5s summary: 157 layers, 7012822 parameters, 0 gradients, 15.8 GFLOPs

PyTorch: starting from yolov5/runs/train/Model/weights/best.pt with output shape (1, 25200, 6) (13.8 MB)

TorchScript: starting export with torch 2.1.0+cu118...
TorchScript: export success ✅ 2.6s, saved as yolov5/runs/train/Model/weights/best.torchscript (27.2 MB)
requirements: Ultralytics requirement ['onnx>=1.12.0'] not found, attempting AutoUpdate...
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.7/15.7 MB 297.6 MB/s eta 0:00:00

In [17]:
# settings
INPUT_WIDTH =  640
INPUT_HEIGHT = 640

In [18]:
img = io.imread('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/TEST/TEST.jpeg')

fig = px.imshow(img)
fig.update_layout(width=700, height=400, margin=dict(l=10, r=10, b=10, t=10))
fig.update_xaxes(showticklabels=False).update_yaxes(showticklabels=False)
fig.show()

In [19]:
# LOAD YOLO MODEL
net = cv2.dnn.readNetFromONNX('./yolov5/runs/train/Model/weights/best.onnx')
net.setPreferableBackend(cv2.dnn.DNN_BACKEND_OPENCV)
net.setPreferableTarget(cv2.dnn.DNN_TARGET_CPU)

In [20]:
def extract_text(image,bbox):
    x,y,w,h = bbox
    roi = image[y:y+h, x:x+w]

    if 0 in roi.shape:
        return 'no number'

    else:
        text = pt.image_to_string(roi)
        text = text.strip()

        return text
def get_detections(img,net):
    # 1.CONVERT IMAGE TO YOLO FORMAT
    image = img.copy()
    row, col, d = image.shape

    max_rc = max(row,col)
    input_image = np.zeros((max_rc,max_rc,3),dtype=np.uint8)
    input_image[0:row,0:col] = image

    # 2. GET PREDICTION FROM YOLO MODEL
    blob = cv2.dnn.blobFromImage(input_image,1/255,(INPUT_WIDTH,INPUT_HEIGHT),swapRB=True,crop=False)
    net.setInput(blob)
    preds = net.forward()
    detections = preds[0]

    return input_image, detections

def non_maximum_supression(input_image,detections):

    # 3. FILTER DETECTIONS BASED ON CONFIDENCE AND PROBABILIY SCORE

    # center x, center y, w , h, conf, proba
    boxes = []
    confidences = []

    image_w, image_h = input_image.shape[:2]
    x_factor = image_w/INPUT_WIDTH
    y_factor = image_h/INPUT_HEIGHT

    for i in range(len(detections)):
        row = detections[i]
        confidence = row[4] # confidence of detecting license plate
        if confidence > 0.4:
            class_score = row[5] # probability score of license plate
            if class_score > 0.25:
                cx, cy , w, h = row[0:4]

                left = int((cx - 0.5*w)*x_factor)
                top = int((cy-0.5*h)*y_factor)
                width = int(w*x_factor)
                height = int(h*y_factor)
                box = np.array([left,top,width,height])

                confidences.append(confidence)
                boxes.append(box)

    # 4.1 CLEAN
    boxes_np = np.array(boxes).tolist()
    confidences_np = np.array(confidences).tolist()

    # 4.2 NMS
    index = cv2.dnn.NMSBoxes(boxes_np,confidences_np,0.25,0.45)

    return boxes_np, confidences_np, index

def drawings(image,boxes_np,confidences_np,index):
    # 5. Drawings
    for ind in index:
        x,y,w,h =  boxes_np[ind]
        bb_conf = confidences_np[ind]
        conf_text = 'plate: {:.0f}%'.format(bb_conf*100)
        license_text = extract_text(image,boxes_np[ind])


        cv2.rectangle(image,(x,y),(x+w,y+h),(255,0,255),2)
        cv2.rectangle(image,(x,y-30),(x+w,y),(255,0,255),-1)
        cv2.rectangle(image,(x,y+h),(x+w,y+h+25),(0,0,0),-1)


        cv2.putText(image,conf_text,(x,y-10),cv2.FONT_HERSHEY_SIMPLEX,0.7,(255,255,255),1)
        cv2.putText(image,license_text,(x,y+h+27),cv2.FONT_HERSHEY_SIMPLEX,0.7,(0,255,0),1)

    return image

In [21]:
def yolo_predictions(img,net):
    # step-1: detections
    input_image, detections = get_detections(img,net)
    # step-2: NMS
    boxes_np, confidences_np, index = non_maximum_supression(input_image, detections)
    # step-3: Drawings
    result_img = drawings(img,boxes_np,confidences_np,index)
    return result_img

In [22]:
img = io.imread('/content/drive/MyDrive/Number_Plate_Detection_Dataset/number_plate_detection_data/TEST/TEST.jpeg')
results = yolo_predictions(img,net)
fig = px.imshow(img)
fig.update_layout(width=700, height=400, margin=dict(l=10, r=10, b=10, t=10))
fig.update_xaxes(showticklabels=False).update_yaxes(showticklabels=False)
fig.show()


In [ ]:
"""To check the full project on my github account : https://github.com/AmenallahBouhachem
we made a user friendly flask web app

"""